# Mecánica Celeste - Trabajo grupal

Usando el código desarrollado en la práctica individual, se ha completado el mismo para tratar de hacer una aplicación más sencilla para el usuario, además de haber incluído algunas funcionalidades nuevas. Dichas funcionalidades se irán comentando a lo largo de la práctica.

In [1]:
from display import SolarSystem, Displayer
import plotly.offline as py
from planet import Planet
import ipywidgets as wdgs
import plotly.graph_objs as go

py.init_notebook_mode(connected=True)

planets_list = [
    Planet("Mercurio", 0.206, 0.387, 87.97, 3.301e23, 7, 47.14, 75.9),
    Planet("Venus", 0.007, 0.723, 224.7, 4.867e24, 3.59, 75.78, 130.15),
    Planet("La tierra", 0.017, 1, 365.26, 6.046e24, 0, 0, 101.22),
    Planet("Marte", 0.093, 1.524, 686.98, 6.417e23, 1.85, 48.78, 101.22),
    Planet("Júpiter", 0.048, 5.203, 4332.6, 1.899e27, 1.31, 99.44, 12.72),
    Planet("Saturno", 0.056, 9.546, 10759, 5.685e26, 2.5, 112.79, 91.09),
    Planet("Urano", 0.047, 19.2, 30687, 8.682e25, 0.77, 73.48, 169.05),
    Planet("Neptuno", 0.009, 30.09, 60784, 1.024e26, 1.78, 130.68, 43.83)    
]

def print_2bodies_solution(planet, time):
    static_pos = planet.position_2d(time)
    pos = planet.get_positions_2bodies(time)
    print("Posición de {} en el día {} sin tomar el problema de los dos cuerpos: {}".format(planet, 
                                                                                            time, 
                                                                                            static_pos))
    print("Posición de {} en el día {} resolviendo el problema de los dos cuerpos: {}".format(planet,
                                                                                              time,
                                                                                              pos[0]))
    print("Posición del Sol en el día {}: {}".format(time, pos[1]))

def print_2bodies_orbit(planet, time):
    xs = planet.get_orbit_2d(200)
    xs_2bodies = planet.get_orbit_2bodies(200)
    
    orbit = go.Scattergl(x=xs[:, 0], y=xs[:, 1],
                         name='órbita')

    orbit_2b = go.Scattergl(x=xs_2bodies[:, 0], y=xs_2bodies[:, 1],
                            name='órbita en el problema de los dos cuerpos')
    
    position = planet.position_2d(time)
    
    planet_pos = go.Scattergl(x=[position[0]], y=[position[1]],
                              mode='markers',
                              marker=dict(
                                  size=15,
                                  color='rgba(152, 0, 0, .8)',
                                  line=dict(
                                      width=2,
                                      color='rgb(0, 0, 0)'
                                  )
                              ),
                              name='{}: día {}'
                             .format(planet.name, time))

    sun = go.Scattergl(x=[0], y=[0],
                       mode='markers',
                       marker=dict(
                           size=20,
                           color='rgba(230, 230, 0, .9)',
                           line=dict(width=1, color='rgb(100,100,0)')
                       ),
                       name='Sol')

    rng = int(1.2*planet.a) + 1

    layout = go.Layout(
        width=700, height=500,
        xaxis=dict(
            anchor='y',
            range=[-rng, rng]
        ),
        yaxis=dict(
            anchor='x',
            autorange=False,
            range=[-rng, rng],
        )
    )
    data = [orbit, orbit_2b, planet_pos, sun]
    fig = go.Figure(data=data, layout=layout)
    py.iplot(fig, filename='plots/orbit_plot')

displayer = Displayer()
solar_system = SolarSystem()

## Información sobre el planeta

En esta primera parte, se ha completado la información que se tiene sobre los planetas, de forma que ahora se toman los mismos en tres dimensiones. Para ello, se resuelve el problema para cada planeta en dos dimensiones, y tras esto, se aplican matrices de rotación, utilizando para ello la tabla de ángulos disponible en el libro guía de la asignatura. Recordamos los elementos que se han calculado:

- Posición del planeta en 3 dimensiones
- Distancia al sol
- Velocidad del planeta
- Módulo de la velocidad
- Anomalía real del planeta (calculada primero usando el método de Runge-Kutta y después a partir de la anomalía excéntrica)
- Energía del planeta, calculada en función del tiempo y utilizando las constantes del problema.
- Momento angular el planeta, primero en función del tiempo y después como constante a partir de las constantes propias del planeta
- Anomalía excéntrica del planeta, primero usando funciones de Bessel y después aproximando el valor por el método de Newton

In [2]:
info_planet_picker = wdgs.Dropdown(options=planets_list, description="Planeta")
info_day_picker = wdgs.FloatText(value=1, description="Día", disabled=False)
wdgs.interact(displayer.print_information, planet=info_planet_picker, time=info_day_picker);

Posición de Mercurio en el día 1.0: [ 0.04245968  0.30389176  0.02155929]
Distancia al sol de Mercurio en el día 1.0: 0.3076001080181024

Velocidad de Mercurio en el día 1.0: [-0.03347827  0.00508486  0.00343784]
Módulo de la velocidad de Mercurio en el día 1.0: 0.034036290379634876

Anomalía real de Mercurio en el día 1.0: 0.11078595025320832
Anomalía real de Mercurio en el día 1.0 (cálculo a partir de la anomalía excéntrica): 0.11078595027110026

Energía de Mercurio en el día 1.0: -0.0003820168218101142
Energía (constante) de Mercurio: -0.00038201682181011393

Momento angular de Mercurio en el día 1.0: [ 0.0009351  -0.00086774  0.01038967]
Módulo del momento angular de Mercurio en el día 1.0: 0.01046769624230092
Módulo del momento angular de Mercurio (constante): 0.010467696242300909

Anomalía excéntrica de Mercurio el día 1.0,calculada usando funciones de Bessel: 0.08992345980365034
Anomalía excéntrica de Mercurio el día 1.0,calculada por el método de Newton: 0.08992345980367325
Dif

## Movimiento orbital de los planetas

Aprovechando el nuevo cálculo de la posición, se han creado dos animaciones. En la primera de ellas tenemos representados los planetas interiores (Mercurio, Venus, La Tierra y Marte) y en la segunda los exteriores (Júpiter, Saturno, Urano y Neptuno). Se ha tomado esta decisión porque colocar los 8 planetas en la misma gráfica producía una visualización difícil, ya que el radio de la órbita de Mercurio es del orden de 100 veces menor que el radio de la órbita de Neptuno.

En ambas gráficas se puede observar cómo las órbitas de los planetas no se encuentran todas en el mismo plano, si no que hay un cierto ángulo de inclinación entre unas y otras.

Al iniciar las animaciones, se visualiza el movimiento de los planetas en función del número de días. De esta forma se comprueba cómo afectan a la rotación los diferentes periodos orbitales. Se toma como referencia el planeta más externo, que es el que tiene un periodo más amplio en ambos casos.

In [3]:
solar_system.display_inner_planets()
solar_system.display_outer_planets()

## Resolución del problema de los dos cuerpos

En este apartado, se ha dado solución al problema de los dos cuerpos. Hasta este momento, habíamos tratado el problema de la órbita de los planetas sin tener en cuenta la atracción que el planeta ejerce sobre el Sol. Esta atracción provoca un desplazamiento sutil del planeta respecto del origen de coordenadas. A continuación se muestra el problema de los dos cuerpos resuelto en dos dimensiones. En el primer desplegable, se puede seleccionar el planeta deseado y el día del periodo orbital en el que se quieren hacer los cálculos, y por pantalla se muestra la posición teórica que ocuparía el planeta sin resolver el problema de los dos cuerpos, la posición que toma al resolverlo, y la posición del Sol, que deja de ser el punto (0,0).

Debado tenemos una gráfica en la que se muestran simultáneamente las dos órbitas, para que se observe la diferencia que hay entre ellas.

In [4]:
planet_picker_2b = wdgs.Dropdown(options=planets_list, description="Planeta")
day_picker_2b = wdgs.FloatText(value=1, description="Día", disabled=False)
wdgs.interact(print_2bodies_solution, planet=planet_picker_2b, time=day_picker_2b);

Posición de Mercurio en el día 1.0 sin tomar el problema de los dos cuerpos: [0.30571436884414377, 0.034008103960343927]
Posición de Mercurio en el día 1.0 resolviendo el problema de los dos cuerpos: [ 0.30664893  0.02158468]
Posición del Sol en el día 1.0: [ -5.09967074e-08  -5.65366815e-09]


In [5]:
orbit_planet_picker = wdgs.Dropdown(options=planets_list, description="Planeta")
orbit_day_picker = wdgs.FloatText(value=1, description="Día", disabled=False)
wdgs.interact(print_2bodies_orbit, planet=orbit_planet_picker, time=orbit_day_picker);